In [2]:
from datasets import load_dataset

dataset = load_dataset("facebook/natural_reasoning")
train_data = dataset["train"].select(range(5000))  # Start with 5k examples


In [3]:
def format_for_training(example):
    return {
        "prompt": example["question"],
        "completion": example["reference_answer"]
    }

train_data = train_data.map(format_for_training)


In [4]:
from transformers import AutoTokenizer

model_checkpoint = "distilgpt2"
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
tokenizer.pad_token = tokenizer.eos_token
max_seq_length = 512

def tokenize(example):
    input_text = f"### Question: {example['prompt']}\n### Answer: {example['completion']}{tokenizer.eos_token}"
    tokenized = tokenizer(
        input_text,
        padding="max_length",
        truncation=True,
        max_length=max_seq_length
    )
    tokenized["labels"] = tokenized["input_ids"].copy()
    return tokenized

tokenized_data = train_data.map(tokenize)


In [5]:
from transformers import AutoModelForCausalLM, TrainingArguments, Trainer

model = AutoModelForCausalLM.from_pretrained(model_checkpoint)

training_args = TrainingArguments(
    output_dir="./my_bot_model",
    evaluation_strategy="no",
    learning_rate=2e-5,
    per_device_train_batch_size=2,
    num_train_epochs=1,
    save_strategy="epoch",
    weight_decay=0.01,
    fp16=True  # You said you have 4GB GPU
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_data,
    tokenizer=tokenizer
)

trainer.train()
model.save_pretrained("./my_bot_model")
tokenizer.save_pretrained("./my_bot_model")


c:\Users\shukl\anaconda3\Lib\site-packages\transformers\training_args.py:1611: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
C:\Users\shukl\AppData\Local\Temp\ipykernel_7600\3538093026.py:16: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
`loss_type=None` was set in the config but it is unrecognised.Using the default loss: `ForCausalLMLoss`.


('./my_bot_model\\tokenizer_config.json',
 './my_bot_model\\special_tokens_map.json',
 './my_bot_model\\vocab.json',
 './my_bot_model\\merges.txt',
 './my_bot_model\\added_tokens.json',
 './my_bot_model\\tokenizer.json')

In [9]:
import torch

model = AutoModelForCausalLM.from_pretrained("./my_bot_model")
tokenizer = AutoTokenizer.from_pretrained("./my_bot_model")

question = "What is the total work done on an object when it is moved upwards against gravity?"
input_text = f"### Question: {question}\n### Answer:"
inputs = tokenizer(input_text, return_tensors="pt").to(model.device)

with torch.no_grad():
    output = model.generate(
        **inputs,
        max_length=256,
        do_sample=True,
        temperature=0.7,
        top_p=0.9,
        top_k=50,
        pad_token_id=tokenizer.eos_token_id
    )

response = tokenizer.decode(output[0], skip_special_tokens=True)
answer = response.replace(input_text, "").strip()

print("💬 Model Answer:\n", answer)


💬 Model Answer:
 The total work done on an object when it is moved upwards against gravity is approximately 3.8x faster than the total work done on an object in a vacuum.
